# Wikipedia

In [1]:
!pip install sklearn-pycrfsuite
!pip install datasets

  Using cached sklearn_pycrfsuite-0.4.0-py2.py3-none-any.whl
  Using cached python-crfsuite-extension-0.9.7.tar.gz (485 kB)
  Running setup.py clean for python-crfsuite-extension
Failed to build python-crfsuite-extension
    Running setup.py install for python-crfsuite-extension: started
    Running setup.py install for python-crfsuite-extension: finished with status 'error'


  ERROR: Command errored out with exit status 1:
   command: 'C:\Users\kvdiv\anaconda3\python.exe' -u -c 'import sys, setuptools, tokenize; sys.argv[0] = '"'"'C:\\Users\\kvdiv\\AppData\\Local\\Temp\\pip-install-o6j04v4w\\python-crfsuite-extension_0dc5c5ea46a148928bd69d80a03f9b61\\setup.py'"'"'; __file__='"'"'C:\\Users\\kvdiv\\AppData\\Local\\Temp\\pip-install-o6j04v4w\\python-crfsuite-extension_0dc5c5ea46a148928bd69d80a03f9b61\\setup.py'"'"';f=getattr(tokenize, '"'"'open'"'"', open)(__file__);code=f.read().replace('"'"'\r\n'"'"', '"'"'\n'"'"');f.close();exec(compile(code, __file__, '"'"'exec'"'"'))' bdist_wheel -d 'C:\Users\kvdiv\AppData\Local\Temp\pip-wheel-5eep5ct1'
       cwd: C:\Users\kvdiv\AppData\Local\Temp\pip-install-o6j04v4w\python-crfsuite-extension_0dc5c5ea46a148928bd69d80a03f9b61\
  Complete output (12 lines):
  running bdist_wheel
  running build
  running build_py
  creating build
  creating build\lib.win-amd64-3.8
  creating build\lib.win-amd64-3.8\pycrfsuite
  copying p

In [2]:
from datasets import load_dataset
import pandas as pd
import numpy as np
import sklearn
import string
from sklearn.model_selection import train_test_split
import nltk

In [3]:
dataset = load_dataset(
    "wikiann", 
    'en' # Select language from the dataset
)

print(f'The dataset is a dictionary with two splits: \n\n{dataset}')

Reusing dataset wikiann (C:\Users\kvdiv\.cache\huggingface\datasets\wikiann\en\1.1.0\4bfd4fe4468ab78bb6e096968f61fab7a888f44f9d3371c2f3fea7e74a5a354e)


  0%|          | 0/3 [00:00<?, ?it/s]

The dataset is a dictionary with two splits: 

DatasetDict({
    validation: Dataset({
        features: ['tokens', 'ner_tags', 'langs', 'spans'],
        num_rows: 10000
    })
    test: Dataset({
        features: ['tokens', 'ner_tags', 'langs', 'spans'],
        num_rows: 10000
    })
    train: Dataset({
        features: ['tokens', 'ner_tags', 'langs', 'spans'],
        num_rows: 20000
    })
})


In [4]:
from datasets import load_dataset
train = load_dataset(
    "wikiann", 
    'en' ,# Select language from the dataset
     split="train",
#ignore_verifications=True,
    #cache_dir=cache_dir,
)
print(f"Training dataset with {len(train)} instances loaded")

Reusing dataset wikiann (C:\Users\kvdiv\.cache\huggingface\datasets\wikiann\en\1.1.0\4bfd4fe4468ab78bb6e096968f61fab7a888f44f9d3371c2f3fea7e74a5a354e)


Training dataset with 20000 instances loaded


In [5]:
from datasets import load_dataset
test = load_dataset(
    "wikiann", 
    'en' ,# Select language from the dataset
     split="test",
#ignore_verifications=True,
    #cache_dir=cache_dir,
)
print(f"Training dataset with {len(test)} instances loaded")

Reusing dataset wikiann (C:\Users\kvdiv\.cache\huggingface\datasets\wikiann\en\1.1.0\4bfd4fe4468ab78bb6e096968f61fab7a888f44f9d3371c2f3fea7e74a5a354e)


Training dataset with 10000 instances loaded


In [6]:
from sklearn.model_selection import train_test_split

train_sentences_ner = dataset["train"]["tokens"]
train_labels_ner = dataset["train"]["ner_tags"]

val_sentences_ner = dataset["validation"]["tokens"]
val_labels_ner = dataset["validation"]["ner_tags"]

test_sentences_ner = dataset["test"]["tokens"]
test_labels_ner = dataset["test"]["ner_tags"]

print(len(train_labels_ner))
print(len(val_labels_ner))
print(len(test_labels_ner))

20000
10000
10000


The train_labels_ner, val_labels_ner and test_labels_ner are currently lists of lists of integers. These integers are the ner_tags: a list of classification labels, with possible values including O (0), B-PER (1), I-PER (2), B-ORG (3), I-ORG (4), B-LOC (5), I-LOC (6). Some methods may require the tags in string format, which we can convert with this function:

In [7]:
def labels_int_to_string(labels):
    mapping = {
        0: 'O',
        1: 'B-PER',
        2: 'I-PER',
        3: 'B-ORG',
        4: 'I-ORG',
        5: 'B-LOC',
        6: 'I-LOC'
    }
    
    return [[mapping[label] for label in doc] for doc in labels]

train_labels_ner = labels_int_to_string(train_labels_ner)
val_labels_ner = labels_int_to_string(val_labels_ner)
test_labels_ner = labels_int_to_string(test_labels_ner)

In [8]:
ner_tag_mapping = {0: 'O', 1:'B-PER', 2:'I-PER', 3:'B-ORG', 4:'I-ORG', 5:'B-LOC', 6:'I-LOC', 7:'B-MISC', 8:'I-MISC'}

In [9]:
train_set = [list(zip(s['tokens'], [ner_tag_mapping[tok] for tok in s['ner_tags']])) for s in train][:-1]
test_set = [list(zip(s['tokens'], [ner_tag_mapping[tok] for tok in s['ner_tags']])) for s in test][:-1]
test_tokens = [s['tokens'] for s in test][:-1]
test_tags = [[ner_tag_mapping[tok] for tok in s['ner_tags']] for s in test][:-1]

In [10]:
train_set

[[('R.H.', 'B-ORG'),
  ('Saunders', 'I-ORG'),
  ('(', 'O'),
  ('St.', 'B-ORG'),
  ('Lawrence', 'I-ORG'),
  ('River', 'I-ORG'),
  (')', 'O'),
  ('(', 'O'),
  ('968', 'O'),
  ('MW', 'O'),
  (')', 'O')],
 [(';', 'O'),
  ("'", 'O'),
  ("''", 'O'),
  ('Anders', 'B-PER'),
  ('Lindström', 'I-PER'),
  ("''", 'O'),
  ("'", 'O')],
 [('Karl', 'B-PER'),
  ('Ove', 'I-PER'),
  ('Knausgård', 'I-PER'),
  ('(', 'O'),
  ('born', 'O'),
  ('1968', 'O'),
  (')', 'O')],
 [('Atlantic', 'B-LOC'),
  ('City', 'I-LOC'),
  (',', 'I-LOC'),
  ('New', 'I-LOC'),
  ('Jersey', 'I-LOC')],
 [('Her', 'O'),
  ('daughter', 'O'),
  ('from', 'O'),
  ('the', 'O'),
  ('second', 'O'),
  ('marriage', 'O'),
  ('was', 'O'),
  ('Marie', 'B-PER'),
  ("d'Agoult", 'I-PER'),
  ('(', 'O'),
  ('1805–1876', 'O'),
  (')', 'O'),
  (',', 'O'),
  ('who', 'O'),
  ('in', 'O'),
  ('turn', 'O'),
  ('gave', 'O'),
  ('birth', 'O'),
  ('to', 'O'),
  ('several', 'O'),
  ('children', 'O'),
  (',', 'O'),
  ('among', 'O'),
  ('them—from', 'O'),
  ('her',

In [11]:
!conda install -c conda-forge python-crfsuite -y

Solving environment: ...working... done

## Package Plan ##

  environment location: C:\Users\kvdiv\anaconda3

  added / updated specs:
    - python-crfsuite


The following packages will be downloaded:

    package                    |            build
    ---------------------------|-----------------
    ca-certificates-2022.6.15  |       h5b45459_0         188 KB  conda-forge
    certifi-2022.6.15          |   py38haa244fe_0         155 KB  conda-forge
    conda-4.13.0               |   py38haa244fe_1        1016 KB  conda-forge
    openssl-1.1.1q             |       h8ffe710_0         5.8 MB  conda-forge
    ------------------------------------------------------------
                                           Total:         7.1 MB

The following packages will be UPDATED:

  ca-certificates                      2021.10.8-h5b45459_0 --> 2022.6.15-h5b45459_0
  certifi                          2021.10.8-py38haa244fe_2 --> 2022.6.15-py38haa244fe_0
  conda                               

In [12]:
print(train_set)

[[('R.H.', 'B-ORG'), ('Saunders', 'I-ORG'), ('(', 'O'), ('St.', 'B-ORG'), ('Lawrence', 'I-ORG'), ('River', 'I-ORG'), (')', 'O'), ('(', 'O'), ('968', 'O'), ('MW', 'O'), (')', 'O')], [(';', 'O'), ("'", 'O'), ("''", 'O'), ('Anders', 'B-PER'), ('Lindström', 'I-PER'), ("''", 'O'), ("'", 'O')], [('Karl', 'B-PER'), ('Ove', 'I-PER'), ('Knausgård', 'I-PER'), ('(', 'O'), ('born', 'O'), ('1968', 'O'), (')', 'O')], [('Atlantic', 'B-LOC'), ('City', 'I-LOC'), (',', 'I-LOC'), ('New', 'I-LOC'), ('Jersey', 'I-LOC')], [('Her', 'O'), ('daughter', 'O'), ('from', 'O'), ('the', 'O'), ('second', 'O'), ('marriage', 'O'), ('was', 'O'), ('Marie', 'B-PER'), ("d'Agoult", 'I-PER'), ('(', 'O'), ('1805–1876', 'O'), (')', 'O'), (',', 'O'), ('who', 'O'), ('in', 'O'), ('turn', 'O'), ('gave', 'O'), ('birth', 'O'), ('to', 'O'), ('several', 'O'), ('children', 'O'), (',', 'O'), ('among', 'O'), ('them—from', 'O'), ('her', 'O'), ('liaison', 'O'), ('to', 'O'), ('Franz', 'B-PER'), ('Liszt', 'I-PER'), ('–-', 'O'), ('Cosima', 'B

In [33]:
print(test_set)

[[('Shortly', 'O'), ('afterward', 'O'), (',', 'O'), ('an', 'O'), ('encouraging', 'O'), ('response', 'O'), ('influenced', 'O'), ('him', 'O'), ('to', 'O'), ('go', 'O'), ('to', 'O'), ('India', 'B-LOC'), (';', 'O'), ('he', 'O'), ('arrived', 'O'), ('at', 'O'), ('Adyar', 'B-LOC'), ('in', 'O'), ('1884', 'O'), ('.', 'O')], [(':', 'O'), ('Kanye', 'B-PER'), ('West', 'I-PER'), ('featuring', 'O'), ('Jamie', 'B-PER'), ('Foxx', 'I-PER'), ('—', 'O'), ('``', 'O'), ('Gold', 'B-ORG'), ('Digger', 'I-ORG'), ("''", 'O'), ('(', 'O'), ('2005', 'O'), (')', 'O')], [('Blacktown', 'B-ORG'), ('railway', 'I-ORG'), ('station', 'I-ORG')], [("''", 'O'), ('Mycalesis', 'B-LOC'), ('perseus', 'I-LOC'), ('lalassis', 'I-LOC'), ("''", 'O'), ('(', 'O'), ('Hewitson', 'O'), (',', 'O'), ('1864', 'O'), (')', 'O')], [('Jonny', 'B-PER'), ('Lee', 'I-PER'), ('Miller', 'I-PER'), ('-', 'O'), ('Eli', 'B-ORG'), ('Stone', 'I-ORG'), ("''", 'O')], [('Tambourissa', 'B-LOC'), ('cocottensis', 'I-LOC'), ("''", 'O'), ('Lorence', 'O')], [('Admis

In [13]:
import nltk

# Train a CRF NER tagger
def train_CRF_NER_tagger(train_set):
    ### WRITE YOUR OWN CODE HERE
    tagger = nltk.tag.CRFTagger()
    tagger.train(train_set, 'model.crf.tagger')
    return tagger  # return the trained model

tagger = train_CRF_NER_tagger(train_set)

In [16]:
predicted_tags = tagger.tag_sents(test_tokens)

In [17]:
def extract_spans(tagged_sents):
    """
    Extract a list of tagged spans for each named entity type, 
    where each span is represented by a tuple containing the 
    start token and end token indexes.
    
    returns: a dictionary containing a list of spans for each entity type.
    """
    spans = {}
        
    for sidx, sent in enumerate(tagged_sents):
        start = -1
        entity_type = None
        for i, (tok, lab) in enumerate(sent):
            if 'B-' in lab:
                start = i
                end = i + 1
                entity_type = lab[2:]
            elif 'I-' in lab:
                end = i + 1
            elif lab == 'O' and start >= 0:
                
                if entity_type not in spans:
                    spans[entity_type] = []
                
                spans[entity_type].append((start, end, sidx))
                start = -1      
        # Sometimes an I-token is the last token in the sentence, so we still have to add the span to the list
        if start >= 0:    
            if entity_type not in spans:
                spans[entity_type] = []
                
            spans[entity_type].append((start, end, sidx))
                
    return spans


def cal_span_level_f1(test_sents, test_sents_with_pred):
    # get a list of spans from the test set labels
    gold_spans = extract_spans(test_sents)

    # get a list of spans predicted by our tagger
    pred_spans = extract_spans(test_sents_with_pred)
    
    # compute the metrics for each class:
    f1_per_class = []
    
    ne_types = gold_spans.keys()  # get the list of named entity types (not the tags)
    
    for ne_type in ne_types:
        # compute the confusion matrix
        true_pos = 0
        false_pos = 0
        
        for span in pred_spans[ne_type]:
            if span in gold_spans[ne_type]:
                true_pos += 1
            else:
                false_pos += 1
                
        false_neg = 0
        for span in gold_spans[ne_type]:
            if span not in pred_spans[ne_type]:
                false_neg += 1
                
        if true_pos + false_pos == 0:
            precision = 0
        else:
            precision = true_pos / float(true_pos + false_pos)
            
        if true_pos + false_neg == 0:
            recall = 0
        else:
            recall = true_pos / float(true_pos + false_neg)
        
        if precision + recall == 0:
            f1 = 0
        else:
            f1 = 2 * precision * recall / (precision + recall)
            
        f1_per_class.append(f1)
        print(f'F1 score for class {ne_type} = {f1}')
        
    print(f'Macro-average f1 score = {np.mean(f1_per_class)}')

cal_span_level_f1(test_set, predicted_tags)

F1 score for class LOC = 0.7012149231265457
F1 score for class PER = 0.7845644983461962
F1 score for class ORG = 0.5861323010360925
Macro-average f1 score = 0.6906372408362782


In [18]:
import re, unicodedata

class CustomCRFTagger(nltk.tag.CRFTagger):
    _current_tokens = None
    
    def _get_features(self, tokens, idx):
            """
            Extract basic features about this word including
                - Current word
                - is it capitalized?
                - Does it have punctuation?
                - Does it have a number?
                - Suffixes up to length 3

            Note that : we might include feature over previous word, next word etc.

            :return: a list which contains the features
            :rtype: list(str)
            """
            token = tokens[idx]

            feature_list = []

            if not token:
                return feature_list

            # Capitalization
            if token[0].isupper():
                feature_list.append("CAPITALIZATION")

            # Number
            if re.search(self._pattern, token) is not None:
                feature_list.append("HAS_NUM")

            # Punctuation
            punc_cat = {"Pc", "Pd", "Ps", "Pe", "Pi", "Pf", "Po"}
            if all(unicodedata.category(x) in punc_cat for x in token):
                feature_list.append("PUNCTUATION")

            # Suffix up to length 3
            if len(token) > 1:
                feature_list.append("SUF_" + token[-1:])
            if len(token) > 2:
                feature_list.append("SUF_" + token[-2:])
            if len(token) > 3:
                feature_list.append("SUF_" + token[-3:])

                
            # Current word
            feature_list.append("WORD_" + token)
            
            ### WRITE YOUR OWN CODE HERE ###
            if idx > 0:
                feature_list.append("PREVWORD_" + tokens[idx-1])
            if idx < len(tokens)-1:
                feature_list.append("NEXTWORD_" + tokens[idx+1])
                
            ####

            return feature_list
                

In [20]:
# Train a CRF NER tagger
def train_CustomCRF_NER_tagger(train_set):
    ### WRITE YOUR OWN CODE HERE
    tagger = CustomCRFTagger()
    tagger.train(train_set, 'model.crf.tagger')
    return tagger  # return the trained model

tagger = train_CustomCRF_NER_tagger(train_set)

In [21]:
predicted_tags = tagger.tag_sents(test_tokens)
cal_span_level_f1(test_set, predicted_tags)

F1 score for class LOC = 0.7012149231265457
F1 score for class PER = 0.7845644983461962
F1 score for class ORG = 0.5861323010360925
Macro-average f1 score = 0.6906372408362782


In [26]:
# *** Improve the CRF NER tagger using parts of speech (see lab 5) as additional features.
class CRFTaggerWithPOS(CustomCRFTagger):
    _current_tokens = None
    
    def _get_features(self, tokens, index):
        """
        Extract the features for a token and append the POS tag as an additional feature.
        """
        basic_features = super()._get_features(tokens, index)
        
        # Get the pos tags for the current sentence and save it
        if tokens != self._current_tokens:
            self._pos_tagged_tokens = nltk.pos_tag(tokens)
            self._current_tokens = tokens
            
            
        ### WRITE YOUR OWN CODE HERE
        basic_features.append(self._pos_tagged_tokens[index][1])
        ###
        
        return basic_features
    

In [27]:
print(tagger)

In [23]:
predicted_tags = tagger.tag_sents(test_tokens)
cal_span_level_f1(test_set, predicted_tags)

F1 score for class LOC = 0.7012149231265457
F1 score for class PER = 0.7845644983461962
F1 score for class ORG = 0.5861323010360925
Macro-average f1 score = 0.6906372408362782


In [28]:
print(CRFTaggerWithPOS(CustomCRFTagger))

In [30]:
print(train_CustomCRF_NER_tagger(train_set))

In [32]:
from mlxtend.plotting import plot_confusion_matrix
 
fig, ax = plot_confusion_matrix(conf_mat=conf_matrix, figsize=(6, 6), cmap=plt.cm.Greens)
plt.xlabel('Predicted_tags', fontsize=18)
plt.ylabel('Actuals', fontsize=18)
plt.title('Confusion Matrix', fontsize=18)
plt.show()

ModuleNotFoundError: No module named 'mlxtend'

In [34]:
print(train)

Dataset({
    features: ['tokens', 'ner_tags', 'langs', 'spans'],
    num_rows: 20000
})


In [35]:
print(test)

Dataset({
    features: ['tokens', 'ner_tags', 'langs', 'spans'],
    num_rows: 10000
})
